 # Questions:
 
 1. Is there any strong or weak correlation between rainfall & price of onion & Tomato ?
 2. Is there any differences of price between states / Regions?
 3. Is there any other factors apart from rainfall on the price of onion & Tomato?
 4. How to analyse the supply & demand and decide which crop to harvest as a farmer?
 5. which region is the best place to sell?
 6. Average price of Onions is 1300. Prove it with 95% confidence level


In [2]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib
%matplotlib inline
import scipy.stats as stats
import warnings
warnings.filterwarnings('ignore')
from collections import Counter

In [81]:
#Pre-defining the default plots
plt.style.use('ggplot')
plt.rcParams['font.size']=65
plt.rcParams['patch.edgecolor']="b"
#To accommodate maximum number of colums in Jupyter
pd.options.display.max_columns = 20

In [3]:
data=pd.read_csv('Onion_Tomato_weekly.csv')

In [98]:
#Glimpse at data
vegetable_price_and_rainfall=pd.DataFrame(data)
vegetable_price_and_rainfall.head()

Year  CW Vegetable  Bangalore Price (Rs./Quintal)  \
0  2015   1     Onion                           1200   
1  2015   2     Onion                           1359   
2  2015   3     Onion                           1208   
3  2015   4     Onion                           1352   
4  2015   5     Onion                           1323   

   Delhi Price (Rs./Quintal)  Hyderabad Price (Rs./Quintal)  \
0                       1462                           1125   
1                       1383                           1260   
2                       1256                            906   
3                       1321                           1130   
4                       1412                           1400   

   Kolkata Price (Rs./Quintal)  Pune Price (Rs./Quintal)  \
0                       1967.0                      1175   
1                       1596.0                      1290   
2                       1771.0                      1167   
3                       1625.0                      1150   
4                       1750.0                      1120   

   Andaman & Nicobar Islands  Arunachal Pradesh  ...  Coastal Andhra Pradesh  \
0                      126.8               30.8  ...                     2.0   
1                      126.8               30.8  ...                     2.0   
2                      126.8               30.8  ...                     2.0   
3                      126.8               30.8  ...                     2.0   
4                      126.8               30.8  ...                     2.0   

   Telangana  Rayalseema  Tamil Nadu  Coastal Karnataka  \
0       17.5         1.9         8.3                1.4   
1       17.5         1.9         8.3                1.4   
2       17.5         1.9         8.3                1.4   
3       17.5         1.9         8.3                1.4   
4       17.5         1.9         8.3                1.4   

   North Interior Karnataka  South Interior Karnataka  Kerala  Lakshadweep  \
0                       2.4                       1.7     3.1          2.2   
1                       2.4                       1.7     3.1          2.2   
2                       2.4                       1.7     3.1          2.2   
3                       2.4                       1.7     3.1          2.2   
4                       2.4                       1.7     3.1          2.2   

   Mean_vegetable_price  
0                1385.8  
1                1377.6  
2                1261.6  
3                1315.6  
4                1401.0  

[5 rows x 45 columns]

step 1: describe the data
Step 2 : plot the data with histogram, box plot, cross plot, heatmap (pearson correlation)
step 3 : check whether the data is normal and variances are equal and decide what tests can be done based on the questions (1 sample z test or t-test) - hypothesis testing
step 4 : Simulation
step 5 : Conclude with the suggestions based on test results

In [99]:
vegetable_price_and_rainfall.shape

(316, 45)

In [106]:
Mean_vegetable_price= vegetable_price_and_rainfall.loc[: ,"Bangalore Price (Rs./Quintal)":"Pune Price (Rs./Quintal)"]
vegetable_price_and_rainfall['Mean_vegetable_price'] = Mean_vegetable_price.mean(axis=1)
Mean_rainfall= vegetable_price_and_rainfall.loc[: ,"Andaman & Nicobar Islands":"Lakshadweep"]
vegetable_price_and_rainfall['Mean_rainfall'] = Mean_rainfall.mean(axis=1)

In [107]:
#Data types
vegetable_price_and_rainfall.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 316 entries, 0 to 315
Data columns (total 46 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   Year                                316 non-null    int64  
 1   CW                                  316 non-null    int64  
 2   Vegetable                           316 non-null    object 
 3   Bangalore Price (Rs./Quintal)       316 non-null    int64  
 4   Delhi Price (Rs./Quintal)           316 non-null    int64  
 5   Hyderabad Price (Rs./Quintal)       316 non-null    int64  
 6   Kolkata Price (Rs./Quintal)         308 non-null    float64
 7   Pune Price (Rs./Quintal)            316 non-null    int64  
 8   Andaman & Nicobar Islands           316 non-null    float64
 9   Arunachal Pradesh                   316 non-null    float64
 10  Assam & Meghalaya                   316 non-null    float64
 11  Naga Mani Mizo Tripura              316 non-n

In [108]:
#Data Structure..this will produce on for categorical values
vegetable_price_and_rainfall.describe()

Year          CW  Bangalore Price (Rs./Quintal)  \
count   316.000000  316.000000                     316.000000   
mean   2015.993671   26.835443                    1506.487342   
std       0.816472   15.228570                    1104.948820   
min    2015.000000    1.000000                     308.000000   
25%    2015.000000   14.000000                     709.750000   
50%    2016.000000   27.000000                    1129.500000   
75%    2017.000000   40.000000                    1905.000000   
max    2017.000000   53.000000                    6667.000000   

       Delhi Price (Rs./Quintal)  Hyderabad Price (Rs./Quintal)  \
count                 316.000000                     316.000000   
mean                 1431.098101                    1225.139241   
std                   810.919079                     943.615586   
min                   381.000000                     290.000000   
25%                   769.750000                     555.000000   
50%                  1262.500000                     907.000000   
75%                  1700.000000                    1555.750000   
max                  4232.000000                    5480.000000   

       Kolkata Price (Rs./Quintal)  Pune Price (Rs./Quintal)  \
count                   308.000000                316.000000   
mean                   2215.873377               1435.670886   
std                    1319.264149               1060.273313   
min                     580.000000                400.000000   
25%                    1200.000000                723.000000   
50%                    1850.500000               1050.000000   
75%                    2846.500000               1733.000000   
max                    7600.000000               5467.000000   

       Andaman & Nicobar Islands  Arunachal Pradesh  Assam & Meghalaya  ...  \
count                 316.000000         316.000000         316.000000  ...   
mean                  236.198101         219.427848         198.849367  ...   
std                   162.915182         186.360709         180.309358  ...   
min                     2.400000           3.400000           1.700000  ...   
25%                   108.300000          33.800000          15.900000  ...   
50%                   236.300000         221.800000         185.300000  ...   
75%                   346.400000         348.200000         332.500000  ...   
max                   604.300000         637.900000         590.900000  ...   

        Telangana  Rayalseema  Tamil Nadu  Coastal Karnataka  \
count  316.000000  316.000000  316.000000         316.000000   
mean    71.206329   65.805696   74.817089         225.291139   
std     88.528707   78.209212   70.142904         303.500936   
min      0.000000    0.000000    0.800000           0.000000   
25%      1.700000    7.900000   21.700000           3.800000   
50%     22.400000   41.500000   63.000000          77.400000   
75%    133.700000   90.800000  108.800000         316.500000   
max    336.300000  383.800000  379.800000         963.100000   

       North Interior Karnataka  South Interior Karnataka      Kerala  \
count                316.000000                316.000000  316.000000   
mean                  51.225316                 77.224051  190.762025   
std                   57.703922                 73.384813  176.660742   
min                    0.000000                  0.000000    0.300000   
25%                    2.400000                  7.700000   33.300000   
50%                   28.700000                 62.800000  152.100000   
75%                   78.400000                136.600000  292.900000   
max                  206.600000                250.300000  595.700000   

       Lakshadweep  Mean_vegetable_price  Mean_rainfall  
count   316.000000            316.000000     316.000000  
mean    119.817722           1560.262184     103.607489  
std     109.742196            968.180121     100.017736  
min       0.500000            517.500000       9.147222  
25%      2

In [109]:
#Looking at the distibution and spread of the data
vegetable_price_and_rainfall.hist(figsize=(150,150), bins=10)
plt.show()

In [110]:
#Looking at missing values
vegetable_price_and_rainfall.isnull().sum()

Year                                  0
CW                                    0
Vegetable                             0
Bangalore Price (Rs./Quintal)         0
Delhi Price (Rs./Quintal)             0
Hyderabad Price (Rs./Quintal)         0
Kolkata Price (Rs./Quintal)           8
Pune Price (Rs./Quintal)              0
Andaman & Nicobar Islands             0
Arunachal Pradesh                     0
Assam & Meghalaya                     0
Naga Mani Mizo Tripura                0
Sub Himalayan West Bengal & Sikkim    0
Gangetic West Bengal                  0
Orissa                                0
Jharkhand                             0
Bihar                                 0
East Uttar Pradesh                    0
West Uttar Pradesh                    0
Uttarakhand                           0
Haryana Delhi & Chandigarh            0
Punjab                                0
Himachal Pradesh                      0
Jammu & Kashmir                       0
West Rajasthan                        0


In [111]:
plt.figure(figsize=(150,150))
corr_matrix = vegetable_price_and_rainfall.corr()
sns.heatmap(corr_matrix, annot=True, fmt='0.2f', annot_kws={'size':10}, cmap=plt.get_cmap("jet"))

In [4]:
import warnings
warnings.filterwarnings('ignore')
sns.distplot(data)

NameError: name 'vegetable_price_and_rainfall' is not defined